In [18]:
import pandas as pd
import boto3

El CSV a insertar tiene las siguientes columnas:
- VALOR
- VOLUMEN
- PRECIO
- TIME

### Crear la tabla

In [14]:
dynamodb = boto3.resource('dynamodb')
table = dynamodb.create_table(
    TableName='ejercicio_precios',
    KeySchema=[
        {
            'AttributeName': 'VALOR',
            'KeyType': 'HASH'
            # Partition key
        },
        {
            'AttributeName': 'TIME',
            'KeyType': 'RANGE'
            # Sort key
        }
    ],
    AttributeDefinitions=[
        {
            'AttributeName': 'VALOR',
            'AttributeType': 'S'
        },
        {
            'AttributeName': 'TIME',
            'AttributeType': 'S'
        }
    ],
    ProvisionedThroughput={
        'ReadCapacityUnits': 10,
        'WriteCapacityUnits': 10
    }
)

### Leer el CSV

In [19]:
datos = pd.read_csv('C:\\Personal\\Documentos\\Master Inteligencia Artificial\\Modulo 3\\05 - Amazon AWS (aws-mia-main)\\market_data\\market_data_proc.csv')
datos

VALOR  VOLUMEN  PRECIO                     TIME
0       SAN        1    5.41  2018-03-19 09:00:18.002
1       SAN       44    5.41  2018-03-19 09:00:18.002
2       SAN       20    5.41  2018-03-19 09:00:18.002
3       SAN       45    5.41  2018-03-19 09:00:18.002
4       SAN       40    5.41  2018-03-19 09:00:18.002
...     ...      ...     ...                      ...
16764   TEF      450    8.12  2018-03-19 17:35:13.002
16765   TEF      932    8.12  2018-03-19 17:35:13.002
16766   TEF     2229    8.12  2018-03-19 17:35:13.002
16767   TEF      887    8.12  2018-03-19 17:35:13.002
16768   TEF     1467    8.12  2018-03-19 17:35:13.002

[16769 rows x 4 columns]

### Convertimos el dataframe a una lista de diccionarios

In [20]:
diccionario = datos.to_dict(orient='records')
diccionario

[{'VALOR': 'SAN',
  'VOLUMEN': 1,
  'PRECIO': 5.41,
  'TIME': '2018-03-19 09:00:18.002'},
 {'VALOR': 'SAN',
  'VOLUMEN': 44,
  'PRECIO': 5.41,
  'TIME': '2018-03-19 09:00:18.002'},
 {'VALOR': 'SAN',
  'VOLUMEN': 20,
  'PRECIO': 5.41,
  'TIME': '2018-03-19 09:00:18.002'},
 {'VALOR': 'SAN',
  'VOLUMEN': 45,
  'PRECIO': 5.41,
  'TIME': '2018-03-19 09:00:18.002'},
 {'VALOR': 'SAN',
  'VOLUMEN': 40,
  'PRECIO': 5.41,
  'TIME': '2018-03-19 09:00:18.002'},
 {'VALOR': 'SAN',
  'VOLUMEN': 10,
  'PRECIO': 5.41,
  'TIME': '2018-03-19 09:00:18.002'},
 {'VALOR': 'SAN',
  'VOLUMEN': 367,
  'PRECIO': 5.41,
  'TIME': '2018-03-19 09:00:18.002'},
 {'VALOR': 'SAN',
  'VOLUMEN': 396,
  'PRECIO': 5.41,
  'TIME': '2018-03-19 09:00:18.002'},
 {'VALOR': 'SAN',
  'VOLUMEN': 223,
  'PRECIO': 5.41,
  'TIME': '2018-03-19 09:00:18.002'},
 {'VALOR': 'SAN',
  'VOLUMEN': 277,
  'PRECIO': 5.41,
  'TIME': '2018-03-19 09:00:18.002'},
 {'VALOR': 'SAN',
  'VOLUMEN': 190,
  'PRECIO': 5.41,
  'TIME': '2018-03-19 09:00:18.00

### Insertamos los registros

In [17]:
from decimal import Decimal

tabla = dynamodb.Table('ejercicio_precios')

respuestas = []
for registro in diccionario:
    respuesta = tabla.put_item(Item={
        'VALOR': registro['VALOR'],
        'TIME': registro['TIME'],
        'VOLUMEN': registro['VOLUMEN'],
        'PRECIO': str(registro['PRECIO'])
    })
    respuestas.add(respuesta)
    
print(respuestas)

{'ResponseMetadata': {'RequestId': '82AE42KH5QAKU37DQR77SDDMM7VV4KQNSO5AEMVJF66Q9ASUAAJG', 'HTTPStatusCode': 200, 'HTTPHeaders': {'server': 'Server', 'date': 'Thu, 13 Oct 2022 16:52:26 GMT', 'content-type': 'application/x-amz-json-1.0', 'content-length': '2', 'connection': 'keep-alive', 'x-amzn-requestid': '82AE42KH5QAKU37DQR77SDDMM7VV4KQNSO5AEMVJF66Q9ASUAAJG', 'x-amz-crc32': '2745614147'}, 'RetryAttempts': 0}}
{'ResponseMetadata': {'RequestId': 'CEIG9QAS048MT4NKNUOOJNBDKNVV4KQNSO5AEMVJF66Q9ASUAAJG', 'HTTPStatusCode': 200, 'HTTPHeaders': {'server': 'Server', 'date': 'Thu, 13 Oct 2022 16:52:26 GMT', 'content-type': 'application/x-amz-json-1.0', 'content-length': '2', 'connection': 'keep-alive', 'x-amzn-requestid': 'CEIG9QAS048MT4NKNUOOJNBDKNVV4KQNSO5AEMVJF66Q9ASUAAJG', 'x-amz-crc32': '2745614147'}, 'RetryAttempts': 0}}
{'ResponseMetadata': {'RequestId': 'RBDNUH5K9T5FCM4UK4J4F6TMQNVV4KQNSO5AEMVJF66Q9ASUAAJG', 'HTTPStatusCode': 200, 'HTTPHeaders': {'server': 'Server', 'date': 'Thu, 13 Oct

KeyboardInterrupt: 

### Leer los datos del Santander

In [22]:
from boto3.dynamodb.conditions import Key

santander = tabla.query(
    KeyConditionExpression=Key('VALOR').eq('SAN')
)

df2 = pd.DataFrame(santander['Items'])
display(df2)

PRECIO                     TIME VALOR VOLUMEN
0      5.41  2018-03-19 09:00:18.002   SAN     300
1     5.407  2018-03-19 09:00:19.350   SAN    7129
2     5.407  2018-03-19 09:00:19.362   SAN   48018
3     5.405  2018-03-19 09:00:19.434   SAN     400
4     5.405  2018-03-19 09:00:19.662   SAN   38400
...     ...                      ...   ...     ...
4654  5.344  2018-03-19 17:29:30.862   SAN     600
4655  5.343  2018-03-19 17:29:39.421   SAN     431
4656  5.344  2018-03-19 17:29:43.475   SAN    1466
4657  5.344  2018-03-19 17:29:58.514   SAN     600
4658  5.359  2018-03-19 17:35:13.002   SAN    1285

[4659 rows x 4 columns]

### Nota:
Hay forma de introducir todos los registros de golpe, en una única instrucción, sin tener que recorrer los _chopocientosmil_ que hay uno a uno.